# Scaling Multi-Objective Bayesian Optimisation using RayTune

This notebook will explore various Multi-Objective Bayesian Optimisation algorithms and evaluate their distributed schedulers for fast, efficient scaling. The task at hand is Neural Architecture Search (NAS), and the following auxiliary frameworks will be used:

1. **Ax**: Abstraction on top of the popular BoTorch library
2. **Optuna**: Uses tree-structured Parzen Estimator (TPE) for Bayesian optimisation

**RayTune** is the scalable optimisation framework that acts as a distributed backbone for these auxiliary algorithms, and helps scale them in distributed environments. The notebook compares their performance on NAS tasks of varying performances, and in particular, probes their scheduling algorithms that control execution and search speed.

In [1]:
import time
import ray
from ray import train, tune
from ray.tune.schedulers import AsyncHyperBandScheduler
from ray.tune.search.optuna import OptunaSearch

## Neural Architecture Search (NAS)

NAS is a high-level optimisation problem that aims to find the most optimal neural network architecture for specific tasks. Naturally, there are several considerations when designing a neural network, such as the tradeoff between model size and performance and the computational complexity of layers. A large search space requires *multi-objective* optimisation, with Bayesian methods being particularly useful because it is infeasible to train and evaluate every possible architecture. 

### With Ax

In [2]:
from dataclasses import dataclass
import tempfile
from filelock import FileLock
import pytorch_lightning as pl
import torch
import torch.nn as nn
import torch.nn.functional as F
from torchvision import transforms
from torchvision.datasets import MNIST
from torch.utils.data import DataLoader, random_split
from ray.train.lightning import (
    RayDDPStrategy,
    RayLightningEnvironment,
    RayTrainReportCallback,
    RayFSDPStrategy,
    prepare_trainer,
)
from torchmetrics import Accuracy
from fvcore.nn import FlopCountAnalysis


@dataclass
class ModelConfig:
    learning_rate: float
    # batch_size: int
    layer_1_size: int
    layer_2_size: int
    layer_3_size: int
    dropout: float


class MNISTClassifier(pl.LightningModule):
    def __init__(self, config):
        super().__init__()
        self.config = config

        self.accuracy = Accuracy(task="multiclass", num_classes=10, top_k=1)

        # model parameters
        self.layer1 = nn.Linear(28 * 28, config.layer_1_size)
        self.layer2 = nn.Linear(config.layer_1_size, config.layer_2_size)
        self.layer3 = nn.Linear(config.layer_2_size, config.layer_3_size)
        self.layer4 = nn.Linear(config.layer_3_size, 10)
        self.dropout = nn.Dropout(config.dropout)

        # training parameters
        self.learning_rate = config.learning_rate

        self.eval_loss = []
        self.eval_accuracy = []

    def forward(self, x):
        batch_size, channels, width, height = x.size()

        x = x.view(batch_size, -1)

        x = F.relu(self.layer1(x))
        x = self.dropout(x)

        x = F.relu(self.layer2(x))
        x = self.dropout(x)

        x = F.relu(self.layer3(x))
        x = self.dropout(x)

        x = self.layer4(x)
        x = torch.log_softmax(x, dim=1)
        return x

    def cross_entropy_loss(self, logits, labels):
        """
        Apply NLL loss because softmax is applied in the forward function
        """
        return F.nll_loss(logits, labels)

    def training_step(self, train_batch, batch_idx):
        x, y = train_batch
        logits = self.forward(x)
        loss = self.cross_entropy_loss(logits, y)
        accuracy = self.accuracy(logits, y)

        self.log("ptl/train_loss", loss)
        self.log("ptl/train_accuracy", accuracy)

        return loss

    def validation_step(self, val_batch, batch_idx):
        x, y = val_batch
        logits = self.forward(x)
        loss = self.cross_entropy_loss(logits, y)
        accuracy = self.accuracy(logits, y)

        self.eval_loss.append(loss)
        self.eval_accuracy.append(accuracy)

        return {"val_loss": loss, "val_accuracy": accuracy}

    def on_validation_epoch_end(self):
        avg_loss = torch.stack(self.eval_loss).mean()
        avg_acc = torch.stack(self.eval_accuracy).mean()
        
        # flop_count = FlopCountAnalysis(self, (1, 1, 28, 28)).total()
        
        self.log("ptl/val_loss", avg_loss, sync_dist=True)
        self.log("ptl/val_accuracy", avg_acc, sync_dist=True)
        # self.log("ptl/flops", flop_count, sync_dist=True)
        self.eval_loss.clear()
        self.eval_accuracy.clear()

    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters(), lr=self.learning_rate)
        return optimizer


class MNISTDataModule(pl.LightningDataModule):
    def __init__(self, batch_size=128):
        super().__init__()
        self.data_dir = tempfile.mkdtemp()
        self.batch_size = batch_size
        self.transform = transforms.Compose(
            [transforms.ToTensor(), transforms.Normalize((0.1307,), (0.3081,))]
        )

    def setup(self, stage=None):
        with FileLock(f"{self.data_dir}.lock"):
            mnist = MNIST(
                self.data_dir, train=True, download=True, transform=self.transform
            )
            self.mnist_train, self.mnist_val = random_split(mnist, [55000, 5000])
            self.mnist_test = MNIST(
                self.data_dir, train=False, download=True, transform=self.transform
            )

    def train_dataloader(self):
        return DataLoader(self.mnist_train, 
                          self.batch_size, num_workers=4)

    def val_dataloader(self):
        return DataLoader(self.mnist_val, batch_size=self.batch_size, num_workers=4)

    def test_dataloader(self):
        return DataLoader(self.mnist_test, batch_size=self.batch_size, num_workers=4)

#### Single-Objective Using AxSearch

In [3]:
from ray.train.torch import TorchTrainer
from ray.train import RunConfig, ScalingConfig, CheckpointConfig

# unnecessary when running on Mac
# scaling_config = ScalingConfig(
#     num_workers=3,
#     use_gpu=True,
#     resources_per_worker={"CPU": 1, "GPU": 1}
# )

# lazy to tune this
BATCH_SIZE = 128

data_module = MNISTDataModule(batch_size=BATCH_SIZE)

def train_func(config):
    print("printing config", config)
    with open("config.txt", "w") as f:
        f.write(str(config))

    # instantiate config object
    config = ModelConfig( 
        learning_rate=config["learning_rate"],
        # batch_size=config["batch_size"],
        layer_1_size=config["layer_1_size"],
        layer_2_size=config["layer_2_size"],
        layer_3_size=config["layer_3_size"],
        dropout=config["dropout"],
    )

    model = MNISTClassifier(config=config)

    trainer = pl.Trainer(
        devices=1,
        accelerator="cpu",
        strategy=RayDDPStrategy(),
        callbacks=[RayTrainReportCallback()],
        plugins=[RayLightningEnvironment()],
        enable_progress_bar=False,
    )

    trainer = prepare_trainer(trainer)
    trainer.fit(model, datamodule=data_module)

run_config = RunConfig(
    checkpoint_config=CheckpointConfig(
        num_to_keep=2,
        checkpoint_score_attribute="ptl/val_accuracy",
        checkpoint_score_order="max"
    )
)

ray_trainer = TorchTrainer(
    train_func,
    # scaling_config=scaling_config,
    run_config=run_config,
)

from ray.tune.schedulers import ASHAScheduler

num_epochs = 5
num_samples = 100

scheduler = ASHAScheduler(
    max_t=num_epochs,
    grace_period=1,
    reduction_factor=2
)

from ray.tune.search.ax import AxSearch

algorithm = AxSearch()
# restrict to 4 concurrent trials
algorithm = tune.search.ConcurrencyLimiter(algorithm, max_concurrent=4)

search_space = {
    "layer_1_size": tune.choice([32, 64, 128]),
    "layer_2_size": tune.choice([64, 128, 256]),
    "layer_3_size": tune.choice([128, 256, 512]),
    "dropout": tune.uniform(0.1, 0.3),
    # "batch_size": tune.choice([32, 64, 128]),
    "learning_rate": tune.loguniform(1e-4, 1e-1),
}

tuner = tune.Tuner(
    ray_trainer,
    param_space={"train_loop_config": search_space},
    tune_config=tune.TuneConfig(
        metric="ptl/val_accuracy",
        mode="max",
        num_samples=num_samples,
        scheduler=scheduler,
    ),
)

result_grid = tuner.fit()

(RayTrainWorker pid=74268) Setting up process group for: env:// [rank=0, world_size=1]
(TorchTrainer pid=74225) Started distributed worker processes: 
(TorchTrainer pid=74225) - (node_id=de5cb2482193b1590b79db7cdad4d55a7af615d633e0f654a77280dc, ip=127.0.0.1, pid=74270) world_rank=0, local_rank=0, node_rank=0
(RayTrainWorker pid=74268) GPU available: True (mps), used: False
(RayTrainWorker pid=74268) TPU available: False, using: 0 TPU cores
(RayTrainWorker pid=74268) HPU available: False, using: 0 HPUs
(RayTrainWorker pid=74268) /Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/pytorch_lightning/trainer/setup.py:177: GPU available but not used. You can set it by doing `Trainer(accelerator='gpu')`.
(RayTrainWorker pid=74268) /Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/pytorch_lightning/loops/utilities.py:73: `max_epochs` was not set. Setting it to 1000 epochs. To train without an epoch limit, set `max_epochs=-1`.


(RayTrainWorker pid=74268) printing config {'layer_1_size': 32, 'layer_2_size': 256, 'layer_3_size': 256, 'dropout': 0.2975844439850506, 'learning_rate': 0.029621658508698624}
(RayTrainWorker pid=74268) Downloading http://yann.lecun.com/exdb/mnist/train-images-idx3-ubyte.gz
(RayTrainWorker pid=74268) Failed to download (trying next):
(RayTrainWorker pid=74268) HTTP Error 403: Forbidden
(RayTrainWorker pid=74268) 
(RayTrainWorker pid=74268) Downloading https://ossci-datasets.s3.amazonaws.com/mnist/train-images-idx3-ubyte.gz
(RayTrainWorker pid=74268) Downloading https://ossci-datasets.s3.amazonaws.com/mnist/train-images-idx3-ubyte.gz to /var/folders/mf/cfzv46p15017stkscsq9jw9h0000gn/T/tmptfihyiis/MNIST/raw/train-images-idx3-ubyte.gz


  0%|          | 0.00/9.91M [00:00<?, ?B/s]
(RayTrainWorker pid=74269) Setting up process group for: env:// [rank=0, world_size=1] [repeated 4x across cluster] (Ray deduplicates logs by default. Set RAY_DEDUP_LOGS=0 to disable log deduplication, or see https://docs.ray.io/en/master/ray-observability/user-guides/configure-logging.html#log-deduplication for more options.)
(TorchTrainer pid=74227) Started distributed worker processes:  [repeated 4x across cluster]
(TorchTrainer pid=74227) - (node_id=de5cb2482193b1590b79db7cdad4d55a7af615d633e0f654a77280dc, ip=127.0.0.1, pid=74269) world_rank=0, local_rank=0, node_rank=0 [repeated 4x across cluster]
(RayTrainWorker pid=74269) GPU available: True (mps), used: False [repeated 4x across cluster]
(RayTrainWorker pid=74269) TPU available: False, using: 0 TPU cores [repeated 4x across cluster]
(RayTrainWorker pid=74269) HPU available: False, using: 0 HPUs [repeated 4x across cluster]
(RayTrainWorker pid=74269) /Users/sidharrthnagappan/.virtualen

(RayTrainWorker pid=74268) Extracting /var/folders/mf/cfzv46p15017stkscsq9jw9h0000gn/T/tmptfihyiis/MNIST/raw/train-images-idx3-ubyte.gz to /var/folders/mf/cfzv46p15017stkscsq9jw9h0000gn/T/tmptfihyiis/MNIST/raw
(RayTrainWorker pid=74270) printing config {'layer_1_size': 32, 'layer_2_size': 64, 'layer_3_size': 512, 'dropout': 0.21022852134227363, 'learning_rate': 0.0001570916990672} [repeated 4x across cluster]
(RayTrainWorker pid=74268) 
(RayTrainWorker pid=74268) Downloading http://yann.lecun.com/exdb/mnist/train-labels-idx1-ubyte.gz
(RayTrainWorker pid=74268) Failed to download (trying next):
(RayTrainWorker pid=74268) HTTP Error 403: Forbidden
(RayTrainWorker pid=74268) 
(RayTrainWorker pid=74268) Downloading https://ossci-datasets.s3.amazonaws.com/mnist/train-labels-idx1-ubyte.gz
(RayTrainWorker pid=74268) Downloading https://ossci-datasets.s3.amazonaws.com/mnist/train-labels-idx1-ubyte.gz to /var/folders/mf/cfzv46p15017stkscsq9jw9h0000gn/T/tmptfihyiis/MNIST/raw/train-labels-idx1-ub

  0%|          | 0.00/28.9k [00:00<?, ?B/s]
100%|██████████| 28.9k/28.9k [00:00<00:00, 93.8kB/s]


...

100%|██████████| 4.54k/4.54k [00:00<00:00, 732kB/s]
(RayTrainWorker pid=74268) 
(RayTrainWorker pid=74268)   | Name     | Type               | Params | Mode 
(RayTrainWorker pid=74268) --------------------------------------------------------
(RayTrainWorker pid=74268) 0 | accuracy | MulticlassAccuracy | 0      | train
(RayTrainWorker pid=74268) 1 | layer1   | Linear             | 25.1 K | train
(RayTrainWorker pid=74268) 2 | layer2   | Linear             | 8.4 K  | train
(RayTrainWorker pid=74268) 3 | layer3   | Linear             | 65.8 K | train
(RayTrainWorker pid=74268) 4 | layer4   | Linear             | 2.6 K  | train
(RayTrainWorker pid=74268) 5 | dropout  | Dropout            | 0      | train
(RayTrainWorker pid=74268) --------------------------------------------------------
(RayTrainWorker pid=74268) 101 K     Trainable params
(RayTrainWorker pid=74268) 0         Non-trainable params
(RayTrainWorker pid=74268) 101 K     Total params
(RayTrainWorker pid=74268) 0.408     Total e

(RayTrainWorker pid=74268) Extracting /var/folders/mf/cfzv46p15017stkscsq9jw9h0000gn/T/tmptfihyiis/MNIST/raw/t10k-labels-idx1-ubyte.gz to /var/folders/mf/cfzv46p15017stkscsq9jw9h0000gn/T/tmptfihyiis/MNIST/raw
(RayTrainWorker pid=74268) 


(RayTrainWorker pid=74270) 
(RayTrainWorker pid=74271) 
(RayTrainWorker pid=74268) /Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:420: Consider setting `persistent_workers=True` in 'train_dataloader' to speed up the dataloader worker initialization.
(RayTrainWorker pid=74271)   | Name     | Type               | Params | Mode  [repeated 4x across cluster]
(RayTrainWorker pid=74271) -------------------------------------------------------- [repeated 8x across cluster]
(RayTrainWorker pid=74271) 0 | accuracy | MulticlassAccuracy | 0      | train [repeated 4x across cluster]
(RayTrainWorker pid=74271) 4 | layer4   | Linear             | 2.6 K  | train [repeated 16x across cluster]
(RayTrainWorker pid=74271) 5 | dropout  | Dropout            | 0      | train [repeated 4x across cluster]
(RayTrainWorker pid=74271) 94.2 K    Trainable params [repeated 4x across cluster]
(RayTrainWorker pid=74271) 0     

(RayTrainWorker pid=75852) printing config {'layer_1_size': 32, 'layer_2_size': 128, 'layer_3_size': 128, 'dropout': 0.29228452969433516, 'learning_rate': 0.015165743871966505}


(RayTrainWorker pid=75852) /Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:420: Consider setting `persistent_workers=True` in 'train_dataloader' to speed up the dataloader worker initialization.
(RayTrainWorker pid=74269) /Users/sidharrthnagappan/.pyenv/versions/3.11.0/lib/python3.11/multiprocessing/resource_tracker.py:224: UserWarning: resource_tracker: There appear to be 54 leaked semaphore objects to clean up at shutdown
(RayTrainWorker pid=74269)   warnings.warn('resource_tracker: There appear to be %d '
(RayTrainWorker pid=74270) Checkpoint successfully created at: Checkpoint(filesystem=local, path=/Users/sidharrthnagappan/ray_results/TorchTrainer_2024-12-26_19-34-45/TorchTrainer_687b9_00003_3_dropout=0.2102,layer_1_size=32,layer_2_size=64,layer_3_size=512,learning_rate=0.0002_2024-12-26_19-34-46/checkpoint_000001)
(RayTrainWorker pid=74271) Traceback (most recent call last):
(RayTrainWorker

#### Multi-Objective Using AxSearchMultiObjective

In [4]:
from lib.axsearch_multiobjective import AxSearchMultiObjective
from lib.ax_torchtrainer import TorchTrainerMultiObjective
from ax.service.ax_client import AxClient
from ray.tune.search import ConcurrencyLimiter
from ax.service.utils.instantiation import ObjectiveProperties
from ray.tune.schedulers import ASHAScheduler
from ray.train.torch import TorchTrainer
from ray.train import RunConfig, ScalingConfig, CheckpointConfig

ax_client = AxClient(verbose_logging=False)

ax_client.create_experiment(
    name="mnist_nas_multiobjective",
    parameters=[
        {"name": "layer_1_size", "type": "choice", "values": [32, 64]},
        {"name": "layer_2_size", "type": "choice", "values": [64, 128]},
        {"name": "layer_3_size", "type": "choice", "values": [128, 256]},
        {"name": "dropout", "type": "range", "bounds": [0.1, 0.3]},
        # {"name": "batch_size", "type": "choice", "values": [32, 64, 128]},
        {"name": "learning_rate", "type": "range", "bounds": [1e-4, 1e-1]},
    ],
    objectives={
        "ptl/val_accuracy": ObjectiveProperties(minimize=False),
        "ptl/val_loss": ObjectiveProperties(minimize=True),
    },
)

algo = AxSearchMultiObjective(ax_client=ax_client)
algo = ConcurrencyLimiter(algo, max_concurrent=4)

num_epochs = 1
num_samples = 100

# ASHAScheduler does not support multi-objective optimization
# scheduler = ASHAScheduler(
#     max_t=num_epochs,
#     grace_period=1,
#     reduction_factor=2
# )

run_config = RunConfig(
    checkpoint_config=CheckpointConfig(
        num_to_keep=2,
        checkpoint_score_attribute="ptl/val_accuracy",
        checkpoint_score_order="max",
    )
)

BATCH_SIZE = 128

data_module = MNISTDataModule(batch_size=BATCH_SIZE)

def train_func(config):
    print("printing config", config)
    with open("config.txt", "w") as f:
        f.write(str(config))

    # instantiate config object
    config = ModelConfig(
        learning_rate=config["learning_rate"],
        # batch_size=config["batch_size"],
        layer_1_size=config["layer_1_size"],
        layer_2_size=config["layer_2_size"],
        layer_3_size=config["layer_3_size"],
        dropout=config["dropout"],
    )

    model = MNISTClassifier(config=config)

    trainer = pl.Trainer(
        devices=10,
        accelerator="cpu",
        strategy=RayDDPStrategy(),
        callbacks=[RayTrainReportCallback()],
        plugins=[RayLightningEnvironment()],
        enable_progress_bar=False,
        max_epochs=1
    )

    trainer = prepare_trainer(trainer)
    trainer.fit(model, datamodule=data_module)


# ray_trainer_wrapper = TorchTrainer(
#     train_func,
#     run_config=run_config,
# )


# def build_trainer(config):
#     config = {
#         "learning_rate": config["learning_rate"],
#         "batch_size": config["batch_size"],
#         "layer_1_size": config["layer_1_size"],
#         "layer_2_size": config["layer_2_size"],
#         "layer_3_size": config["layer_3_size"],
#         "dropout": config["dropout"],
#     }
#     return TorchTrainer(
#         train_func,
#         run_config=run_config,
#         train_loop_config=config,
#     ).as_trainable()


ray_trainer = TorchTrainerMultiObjective(
    train_func,
    # scaling_config=scaling_config,
    run_config=run_config,
)

tuner = tune.Tuner(
    ray_trainer,
    # param_space={"train_loop_config": search_space},
    tune_config=tune.TuneConfig(
        num_samples=100,
        search_alg=algo,
        # scheduler=scheduler,
    ),
    run_config=run_config,
)

ax_multiobjective_result = tuner.fit()

observations []
observation_features []
Suggested config: {'layer_1_size': 32, 'layer_2_size': 64, 'layer_3_size': 256, 'dropout': 0.1540646255016327, 'learning_rate': 0.0005136704654432833}


/Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/ax/modelbridge/cross_validation.py:463: UserWarning: Encountered exception in computing model fit quality: RandomModelBridge does not support prediction.
  warn("Encountered exception in computing model fit quality: " + str(e))


observations []
observation_features []
Suggested config: {'layer_1_size': 64, 'layer_2_size': 128, 'layer_3_size': 128, 'dropout': 0.22378303594887256, 'learning_rate': 0.07835054099448026}
(TorchTrainerMultiObjective pid=93282) train_loop_config:  {'layer_1_size': 32, 'layer_2_size': 64, 'layer_3_size': 256, 'dropout': 0.1540646255016327, 'learning_rate': 0.0005136704654432833}


/Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/ax/modelbridge/cross_validation.py:463: UserWarning: Encountered exception in computing model fit quality: RandomModelBridge does not support prediction.
  warn("Encountered exception in computing model fit quality: " + str(e))
(RayTrainWorker pid=93319) Setting up process group for: env:// [rank=0, world_size=1]


observations []
observation_features []
Suggested config: {'layer_1_size': 64, 'layer_2_size': 64, 'layer_3_size': 256, 'dropout': 0.13932334166020155, 'learning_rate': 0.055660771895386284}


...

(TorchTrainerMultiObjective pid=11529) Started distributed worker processes: 
(TorchTrainerMultiObjective pid=11529) - (node_id=c54eccb9151165c3ae7807ac6b84bd1cd123d80ed3150ee5f65b52d3, ip=127.0.0.1, pid=11601) world_rank=0, local_rank=0, node_rank=0
(RayTrainWorker pid=11601) Setting up process group for: env:// [rank=0, world_size=1]


(RayTrainWorker pid=11601) printing config {'layer_1_size': 64, 'layer_2_size': 128, 'layer_3_size': 256, 'dropout': 0.1, 'learning_rate': 0.002597713228628288}


(RayTrainWorker pid=11601) GPU available: True (mps), used: False
(RayTrainWorker pid=11601) TPU available: False, using: 0 TPU cores
(RayTrainWorker pid=11601) HPU available: False, using: 0 HPUs
(RayTrainWorker pid=11601) /Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/pytorch_lightning/trainer/setup.py:177: GPU available but not used. You can set it by doing `Trainer(accelerator='gpu')`.
(RayTrainWorker pid=11601) 
(RayTrainWorker pid=11601)   | Name     | Type               | Params | Mode 
(RayTrainWorker pid=11601) --------------------------------------------------------
(RayTrainWorker pid=11601) 0 | accuracy | MulticlassAccuracy | 0      | train
(RayTrainWorker pid=11601) 1 | layer1   | Linear             | 50.2 K | train
(RayTrainWorker pid=11601) 2 | layer2   | Linear             | 8.3 K  | train
(RayTrainWorker pid=11601) 3 | layer3   | Linear             | 33.0 K | train
(RayTrainWorker pid=11601) 4 | layer4   | Linear             | 2.6 K

Result: {'ptl/train_loss': 0.22770775854587555, 'ptl/train_accuracy': 0.9090909361839294, 'ptl/val_loss': 0.1629316508769989, 'ptl/val_accuracy': 0.949414074420929, 'epoch': 0, 'step': 430, 'timestamp': 1735215145, 'checkpoint_dir_name': 'checkpoint_000000', 'should_checkpoint': True, 'done': True, 'training_iteration': 1, 'trial_id': 'd304ff59', 'date': '2024-12-26_20-12-25', 'time_this_iter_s': 10.277565240859985, 'time_total_s': 10.277565240859985, 'pid': 11529, 'hostname': 'SidharrhsMBP234', 'node_ip': '127.0.0.1', 'time_since_restore': 10.277565240859985, 'iterations_since_restore': 1, 'experiment_tag': '100_dropout=0.1000,layer_1_size=64,layer_2_size=128,layer_3_size=256,learning_rate=0.0026', 'config/layer_1_size': 64, 'config/layer_2_size': 128, 'config/layer_3_size': 256, 'config/dropout': 0.1, 'config/learning_rate': 0.002597713228628288}
Metrics to include: ['ptl/val_accuracy', 'ptl/val_loss']
Metric dict after trial: {'ptl/val_accuracy': (0.949414074420929, None), 'ptl/val_

2024-12-26 20:12:27,893	INFO tune.py:1041 -- Total run time: 1041.45 seconds (1041.34 seconds for the tuning loop).


In [6]:
ax_multiobjective_result.get_best_result(metric="ptl/val_accuracy", mode="max")

Result(
  metrics={'ptl/train_loss': 0.17368647456169128, 'ptl/train_accuracy': 0.9204545617103577, 'ptl/val_loss': 0.14129841327667236, 'ptl/val_accuracy': 0.9595702886581421, 'epoch': 0, 'step': 430},
  path='/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-26_19-55-05/TorchTrainerMultiObjective_8553cc45_71_dropout=0.1000,layer_1_size=64,layer_2_size=128,layer_3_size=256,learning_rate=0.0028_2024-12-26_20-07-07',
  filesystem='local',
  checkpoint=Checkpoint(filesystem=local, path=/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-26_19-55-05/TorchTrainerMultiObjective_8553cc45_71_dropout=0.1000,layer_1_size=64,layer_2_size=128,layer_3_size=256,learning_rate=0.0028_2024-12-26_20-07-07/checkpoint_000000)
)

In [7]:
ax_multiobjective_result.get_best_result(metric="ptl/val_loss", mode="min")

Result(
  metrics={'ptl/train_loss': 0.09187097102403641, 'ptl/train_accuracy': 0.9659090638160706, 'ptl/val_loss': 0.1371430605649948, 'ptl/val_accuracy': 0.957812488079071, 'epoch': 0, 'step': 430},
  path='/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-26_19-55-05/TorchTrainerMultiObjective_cae30a0e_78_dropout=0.1000,layer_1_size=64,layer_2_size=128,layer_3_size=256,learning_rate=0.0025_2024-12-26_20-08-16',
  filesystem='local',
  checkpoint=Checkpoint(filesystem=local, path=/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-26_19-55-05/TorchTrainerMultiObjective_cae30a0e_78_dropout=0.1000,layer_1_size=64,layer_2_size=128,layer_3_size=256,learning_rate=0.0025_2024-12-26_20-08-16/checkpoint_000000)
)

In [14]:
from lib.mobo_asha_3 import MultiObjectiveAsyncHyperBandScheduler

from lib.axsearch_multiobjective import AxSearchMultiObjective
from lib.ax_torchtrainer import TorchTrainerMultiObjective
from ax.service.ax_client import AxClient
from ray.tune.search import ConcurrencyLimiter
from ax.service.utils.instantiation import ObjectiveProperties
from ray.tune.schedulers import ASHAScheduler
from ray.train.torch import TorchTrainer
from ray.train import RunConfig, ScalingConfig, CheckpointConfig

ax_client_2 = AxClient(verbose_logging=False)

ax_client_2.create_experiment(
    name="mnist_nas_multiobjective_scheduled",
    parameters=[
        {"name": "layer_1_size", "type": "choice", "values": [32, 64]},
        {"name": "layer_2_size", "type": "choice", "values": [64, 128]},
        {"name": "layer_3_size", "type": "choice", "values": [128, 256]},
        {"name": "dropout", "type": "range", "bounds": [0.1, 0.3]},
        # {"name": "batch_size", "type": "choice", "values": [32, 64, 128]},
        {"name": "learning_rate", "type": "range", "bounds": [1e-4, 1e-1]},
    ],
    objectives={
        "ptl/val_accuracy": ObjectiveProperties(minimize=False),
        "ptl/val_loss": ObjectiveProperties(minimize=True),
    },
)

algo_2 = AxSearchMultiObjective(ax_client=ax_client_2)
algo_2 = ConcurrencyLimiter(algo_2, max_concurrent=4)

num_epochs = 1
num_samples = 100

# ASHAScheduler does not support multi-objective optimization
# scheduler = ASHAScheduler(
#     max_t=num_epochs,
#     grace_period=1,
#     reduction_factor=2
# )
scheduler_2 = MultiObjectiveAsyncHyperBandScheduler(
    max_t=num_epochs,
    objectives={
        "ptl/val_accuracy": "max",
        "ptl/val_loss": "min",
    }
)

run_config_2 = RunConfig(
    checkpoint_config=CheckpointConfig(
        num_to_keep=2,
        checkpoint_score_attribute="ptl/val_accuracy",
        checkpoint_score_order="max",
    )
)

BATCH_SIZE = 128

data_module = MNISTDataModule(batch_size=BATCH_SIZE)

def train_func(config):
    print("printing config", config)
    with open("config.txt", "w") as f:
        f.write(str(config))

    # instantiate config object
    config = ModelConfig(
        learning_rate=config["learning_rate"],
        # batch_size=config["batch_size"],
        layer_1_size=config["layer_1_size"],
        layer_2_size=config["layer_2_size"],
        layer_3_size=config["layer_3_size"],
        dropout=config["dropout"],
    )

    model = MNISTClassifier(config=config)

    trainer = pl.Trainer(
        devices=10,
        accelerator="cpu",
        strategy=RayDDPStrategy(),
        callbacks=[RayTrainReportCallback()],
        plugins=[RayLightningEnvironment()],
        enable_progress_bar=False,
        max_epochs=3
    )

    trainer = prepare_trainer(trainer)
    trainer.fit(model, datamodule=data_module)


# ray_trainer_wrapper = TorchTrainer(
#     train_func,
#     run_config=run_config,
# )


# def build_trainer(config):
#     config = {
#         "learning_rate": config["learning_rate"],
#         "batch_size": config["batch_size"],
#         "layer_1_size": config["layer_1_size"],
#         "layer_2_size": config["layer_2_size"],
#         "layer_3_size": config["layer_3_size"],
#         "dropout": config["dropout"],
#     }
#     return TorchTrainer(
#         train_func,
#         run_config=run_config,
#         train_loop_config=config,
#     ).as_trainable()


ray_trainer_2 = TorchTrainerMultiObjective(
    train_func,
    # scaling_config=scaling_config,
    run_config=run_config,
)

tuner_2 = tune.Tuner(
    ray_trainer_2,
    # param_space={"train_loop_config": search_space},
    tune_config=tune.TuneConfig(
        num_samples=100,
        search_alg=algo_2,
        scheduler=scheduler_2,
    ),
    run_config=run_config_2,
)

ax_multiobjective_result_scheduled = tuner_2.fit()

observations []
observation_features []
Suggested config: {'layer_1_size': 32, 'layer_2_size': 64, 'layer_3_size': 256, 'dropout': 0.11164454445242883, 'learning_rate': 0.09583099569678308}


/Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/ax/modelbridge/cross_validation.py:463: UserWarning: Encountered exception in computing model fit quality: RandomModelBridge does not support prediction.
  warn("Encountered exception in computing model fit quality: " + str(e))


observations []
observation_features []
Suggested config: {'layer_1_size': 64, 'layer_2_size': 128, 'layer_3_size': 128, 'dropout': 0.23570580706000327, 'learning_rate': 0.015648011231049894}


(TorchTrainerMultiObjective pid=30540) train_loop_config:  {'layer_1_size': 32, 'layer_2_size': 64, 'layer_3_size': 256, 'dropout': 0.11164454445242883, 'learning_rate': 0.09583099569678308}


/Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/ax/modelbridge/cross_validation.py:463: UserWarning: Encountered exception in computing model fit quality: RandomModelBridge does not support prediction.
  warn("Encountered exception in computing model fit quality: " + str(e))


...

(RayTrainWorker pid=54379) printing config {'layer_1_size': 64, 'layer_2_size': 64, 'layer_3_size': 128, 'dropout': 0.1, 'learning_rate': 0.005532259958714839}


(RayTrainWorker pid=54379) /Users/sidharrthnagappan/.virtualenvs/lsdp_miniproject/lib/python3.11/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:420: Consider setting `persistent_workers=True` in 'train_dataloader' to speed up the dataloader worker initialization.
(RayTrainWorker pid=54379) Checkpoint successfully created at: Checkpoint(filesystem=local, path=/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-27_05-19-11/TorchTrainerMultiObjective_e93f0c83_100_dropout=0.1000,layer_1_size=64,layer_2_size=64,layer_3_size=128,learning_rate=0.0055_2024-12-27_05-40-51/checkpoint_000000)
(RayTrainWorker pid=54379) Traceback (most recent call last):
(RayTrainWorker pid=54379)   File "<string>", line 1, in <module>
(RayTrainWorker pid=54379)   File "/Users/sidharrthnagappan/.pyenv/versions/3.11.0/lib/python3.11/multiprocessing/spawn.py", line 120, in spawn_main
(RayTrainWorker pid=54379)     exitcode = _main(fd, parent_sentinel)
(RayTrainWorker pid=543

2024-12-27 05:41:03,601	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-27_05-19-11' in 0.0739s.


Trial e93f0c83 is not promotable
Result: {'ptl/train_loss': 0.2011377364397049, 'ptl/train_accuracy': 0.9545454382896423, 'ptl/val_loss': 0.20185287296772003, 'ptl/val_accuracy': 0.9398437738418579, 'epoch': 0, 'step': 430, 'timestamp': 1735249263, 'checkpoint_dir_name': 'checkpoint_000000', 'should_checkpoint': True, 'done': True, 'training_iteration': 1, 'trial_id': 'e93f0c83', 'date': '2024-12-27_05-41-03', 'time_this_iter_s': 8.824342012405396, 'time_total_s': 8.824342012405396, 'pid': 54320, 'hostname': 'SidharrhsMBP234', 'node_ip': '127.0.0.1', 'time_since_restore': 8.824342012405396, 'iterations_since_restore': 1, 'experiment_tag': '100_dropout=0.1000,layer_1_size=64,layer_2_size=64,layer_3_size=128,learning_rate=0.0055', 'config/layer_1_size': 64, 'config/layer_2_size': 64, 'config/layer_3_size': 128, 'config/dropout': 0.1, 'config/learning_rate': 0.005532259958714839}
Metrics to include: ['ptl/val_accuracy', 'ptl/val_loss']
Metric dict after trial: {'ptl/val_accuracy': (0.9398

2024-12-27 05:41:03,614	INFO tune.py:1041 -- Total run time: 1312.30 seconds (1312.21 seconds for the tuning loop).


In [15]:
ax_multiobjective_result_scheduled.get_best_result(metric="ptl/val_accuracy", mode="max")

Result(
  metrics={'ptl/train_loss': 0.23043769598007202, 'ptl/train_accuracy': 0.9545454382896423, 'ptl/val_loss': 0.12870284914970398, 'ptl/val_accuracy': 0.962695300579071, 'epoch': 2, 'step': 1290},
  path='/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-27_05-19-11/TorchTrainerMultiObjective_e73d9a21_97_dropout=0.1000,layer_1_size=64,layer_2_size=64,layer_3_size=128,learning_rate=0.0058_2024-12-27_05-39-56',
  filesystem='local',
  checkpoint=Checkpoint(filesystem=local, path=/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-27_05-19-11/TorchTrainerMultiObjective_e73d9a21_97_dropout=0.1000,layer_1_size=64,layer_2_size=64,layer_3_size=128,learning_rate=0.0058_2024-12-27_05-39-56/checkpoint_000002)
)

In [17]:
ax_multiobjective_result_scheduled.get_best_result(metric="ptl/val_loss", mode="min")

Result(
  metrics={'ptl/train_loss': 0.23043769598007202, 'ptl/train_accuracy': 0.9545454382896423, 'ptl/val_loss': 0.12870284914970398, 'ptl/val_accuracy': 0.962695300579071, 'epoch': 2, 'step': 1290},
  path='/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-27_05-19-11/TorchTrainerMultiObjective_e73d9a21_97_dropout=0.1000,layer_1_size=64,layer_2_size=64,layer_3_size=128,learning_rate=0.0058_2024-12-27_05-39-56',
  filesystem='local',
  checkpoint=Checkpoint(filesystem=local, path=/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-27_05-19-11/TorchTrainerMultiObjective_e73d9a21_97_dropout=0.1000,layer_1_size=64,layer_2_size=64,layer_3_size=128,learning_rate=0.0058_2024-12-27_05-39-56/checkpoint_000002)
)

In [18]:
ax_multiobjective_result.get_best_result(metric="ptl/val_accuracy", mode="max")

Result(
  metrics={'ptl/train_loss': 0.17368647456169128, 'ptl/train_accuracy': 0.9204545617103577, 'ptl/val_loss': 0.14129841327667236, 'ptl/val_accuracy': 0.9595702886581421, 'epoch': 0, 'step': 430},
  path='/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-26_19-55-05/TorchTrainerMultiObjective_8553cc45_71_dropout=0.1000,layer_1_size=64,layer_2_size=128,layer_3_size=256,learning_rate=0.0028_2024-12-26_20-07-07',
  filesystem='local',
  checkpoint=Checkpoint(filesystem=local, path=/Users/sidharrthnagappan/ray_results/TorchTrainerMultiObjective_2024-12-26_19-55-05/TorchTrainerMultiObjective_8553cc45_71_dropout=0.1000,layer_1_size=64,layer_2_size=128,layer_3_size=256,learning_rate=0.0028_2024-12-26_20-07-07/checkpoint_000000)
)